The analysis in  Figs. 2–4 of Kornhuber et al. 2024 (PNAS) proceeds from yearly 98th and 87.5th percentiles of tasmax (daily-max. temperature at 2 meters) in observational datasets and CMIP6 HighResMIP model runs (covering the period 1958–2022, with model data concatenated across 2014 by matching member ID). This code produces all panels in Fig. 2–4 if appropriate data is given.

# Imports etc.

In [51]:
## import dask
from dask.distributed import Client, LocalCluster
import numpy as np
import xarray as xr
import matplotlib.pyplot as plt
from matplotlib.lines import Line2D
from matplotlib import ticker
from matplotlib import colors as cm
import matplotlib_inline
import matplotlib.patheffects as pe
%config InlineBackend.figure_format='retina'
import intake
from ecgtools import Builder
from ecgtools.parsers import parse_cmip6
import glob
import pathlib
from xmip.preprocessing import rename_cmip6
from xmip.preprocessing import combined_preprocessing
from dask.diagnostics import ProgressBar
pbar = ProgressBar()
import cartopy
import cartopy.crs as ccrs
import cartopy.feature as cfeature
from cartopy.util import add_cyclic_point
import seaborn as sns
import os
import xesmf as xe
import copy
import pandas as pd
from string import ascii_lowercase
from scipy import stats
import scipy.signal as ss
import statsmodels.stats as sms
tinv = lambda p, df: abs(stats.t.ppf(p/2, df))
from scipy.stats import linregress

def scipylinregress_pval(x,y):
    slope, intercept, r, p, se = linregress(x, y)
    return p
def scipylinregress_slope(x,y):
    slope, intercept, r, p, se = linregress(x, y)
    return slope
def scipylinregress_sterr(x,y):
    slope, intercept, r, p, se = linregress(x, y)
    return se
def weighted_mean(var, wts):
    """Calculates the weighted mean"""
    return np.average(var, weights=wts)
def weighted_variance(var, wts):
    """Calculates the weighted variance"""
    return np.average((var - weighted_mean(var, wts))**2, weights=wts)
def weighted_skew(var, wts):
    """Calculates the weighted skewness"""
    return (np.average((var - weighted_mean(var, wts))**3, weights=wts) /
            weighted_variance(var, wts)**(1.5))

# https://github.com/darothen/plot-all-in-ncfile/blob/master/plot_util.py
def cyclic_dataarray(da, coord):#='longitude'):
    """ Add a cyclic coordinate point to a DataArray along a specified
    named coordinate dimension.
    """
    assert isinstance(da, xr.DataArray)

    lon_idx = da.dims.index(coord)
    cyclic_data, cyclic_coord = add_cyclic_point(da.values,
                                                 coord=da.coords[coord],
                                                 axis=lon_idx)

    # Copy and add the cyclic coordinate and data
    new_coords = dict(da.coords)
    new_coords[coord] = cyclic_coord
    new_values = cyclic_data

    new_da = xr.DataArray(new_values, dims=da.dims, coords=new_coords)

    # Copy the attributes for the re-constructed data and coords
    for att, val in da.attrs.items():
        new_da.attrs[att] = val
    for c in da.coords:
        for att in da.coords[c].attrs:
            new_da.coords[c].attrs[att] = da.coords[c].attrs[att]

    return new_da

# func to convert discrete model/obs files on different grids (in one directory) to single xarray dataset on common grid
def regrid_and_concat(path,filenames,varname,res):
    # collect files in dictionary:
    dct = {}
    for filename in filenames:
        dct.update({filename[:-3]: xr.open_dataset(path + filename)[varname]})
    key_da = xr.DataArray(list(dct.keys()), dims='key', coords={'key': list(dct.keys())})
    # regrid all to same grid:
    ds_out_grid = xr.Dataset({'latitude': (['latitude'], np.arange(-90+res/2, 90, res), {'units':'degrees_north'}),
                              'longitude': (['longitude'], np.arange(0+res/2, 360, res), {'units':'degrees_east'})})
    lst = []; count = 1
    for (k,ds) in dct.items():
        model_id = k.split('.')[2]
        ds_in = ds.rename({'x':'longitude','y':'latitude'})
        for coord in list(ds_in.coords):
            if coord in ['lat','lon']:
                ds_in = ds_in.drop(coord)
        regridder = xe.Regridder(ds_in, ds_out_grid, 'conservative', weights=f'/data0/samuelb/regridders/{model_id}_to_{res}deg.nc')
        ds_out = regridder(ds_in, keep_attrs=True)
        lst.append(ds_out)
        print(count); count+=1
        print(k)
    # concat by key:
    ds = xr.concat(lst, dim=key_da).compute()
    return ds

def detrend_dim(da, dim, deg=1):
    p = da.polyfit(dim=dim, deg=deg)
    fit = xr.polyval(da[dim], p.polyfit_coefficients)
    return da - fit 

def hue_regplot(data, x, y, hue, palette=None, **kwargs):
    
    regplots = []
    
    levels = data[hue].unique()
    
    if palette is None:
        default_colors = plt.get_cmap('tab10')
        palette = {k: default_colors(i) for i, k in enumerate(levels)}
    
    for key in levels:
        regplots.append(
            sns.regplot(
                x=x,
                y=y,
                data=data[data[hue] == key],
                color=palette[key],
                line_kws={'lw':1,'ls':obsls[key],'zorder':503},
                **kwargs
            )
        )
    
    return regplots

matplotlib_inline.backend_inline.set_matplotlib_formats('pdf')
plt.rcParams['pdf.fonttype'] = 42
plt.rcParams['hatch.linewidth'] = .25


# Load data

### Some parameters

In [2]:
forcedexperiment = 'highresSST-present_highresSST-future'
coupledexperiment = 'hist-1950_highres-future'
startyear = 1958
endyear = 2022
res = 1
upperptile = 99#'max'
upperptilenum = 99
lowerptile = 87.5
lowerptilenum = 87.5
singleptilenum = 100 #87.5
trendtype = f'{upperptile}minus{lowerptile}'
trendcovariate = 'year'; trendfactor = 10

ds_out_grid = xr.Dataset({'latitude': (['latitude'], np.arange(-90+res/2, 90, res), {'units':'degrees_north'}),'longitude': (['longitude'], np.arange(0+res/2, 360, res), {'units':'degrees_east'})})
weights = np.cos(np.deg2rad(ds_out_grid.latitude)); weights.name = "weights"


### Load model/obs yearly percentiles

In [8]:
# Regrid and concat model and obs percentiles

varname = 'tx'; varname2 = 'tasmax'
path = f'/data0/samuelb/percs/{varname}/'
filenames_models_and_obs = [i for i in os.listdir(path) if (i[-3:] == '.nc') & (i[-8:-3] != '_0.75')] # ALL MODELS AND ALL OBS
filenames_obs = [i for i in filenames_models_and_obs if i.split('.')[2] == 'ERA5'] # JUST ERA5
# filenames_obs = [i for i in filenames_models_and_obs if i.split('.')[2] in ['ERA5','JRA55_6hr','nclimgrid','eobs']] # ALL OBS
filenames_obs.extend(['JRA.25 km.JRA55_6hr.1958-2022.nc','ECA.25 km.eobs.1950-2022.nc'])#,'NCEI.25 km.nclimgrid.1951-2022.nc','NASA.25 km.MERRA2.1980-2022.nc'])
filenames_models = [i for i in filenames_models_and_obs if i.split('.')[2] not in ['ERA5','JRA55_3hr','JRA55_6hr','nclimgrid','eobs','MERRA2']] # EXCLUDE ALL OBS
filenames_models = [filename for filename in filenames_models if ('CESM2-CAM6' not in filename) and ('ECHAM5' not in filename)] # EXCLUDE LEs
print(filenames_obs); print('\n'.join(['.'.join(i.split('.')[:]) for i in filenames_models])); print(len(filenames_models))
percs_models = regrid_and_concat(path,filenames_models,varname2,res); percs_models = percs_models.assign_coords(longitude = (percs_models.coords['longitude'] + 180) % 360 - 180).sortby('longitude')
percs_obs = regrid_and_concat(path,filenames_obs,varname2,res); percs_obs = percs_obs.where(percs_obs!=0).assign_coords(longitude = (percs_obs.coords['longitude'] + 180) % 360 - 180).sortby('longitude')


['ECMWF.25 km.ERA5.1950-2022.nc', 'JRA.25 km.JRA55_6hr.1958-2022.nc', 'ECA.25 km.eobs.1950-2022.nc']
EC-Earth-Consortium.50 km.EC-Earth3P-HR.r1i1p2f1.gr.hist-1950_highres-future_1950-2022.nc
CNRM-CERFACS.250 km.CNRM-CM6-1.r2i1p1f2.gr.highresSST-present_highresSST-future_1950-2022.nc
MOHC.100 km.HadGEM3-GC31-MM.r1i2p1f1.gn.hist-1950_highres-future_1950-2022.nc
CNRM-CERFACS.250 km.CNRM-CM6-1.r10i1p1f2.gr.highresSST-present_highresSST-future_1950-2022.nc
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r3i1p1f2.gr.highresSST-present_highresSST-future_1950-2022.nc
CNRM-CERFACS.250 km.CNRM-CM6-1.r3i1p1f2.gr.highresSST-present_highresSST-future_1950-2022.nc
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r2i1p1f2.gr.highresSST-present_highresSST-future_1950-2022.nc
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r10i1p1f2.gr.highresSST-present_highresSST-future_1950-2022.nc
AS-RCEC.50 km.HiRAM-SIT-LR.r1i1p1f1.gn.highresSST-present_highresSST-future_1950-2022.nc
MOHC.250 km.HadGEM3-GC31-LL.r1i3p1f1.gn.hist-1950_highres-future_1950-2022.n

/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/smm.py:130: UserWarning: Input array is not C_CONTIGUOUS. Will affect performance.
  warnings.warn('Input array is not C_CONTIGUOUS. ' 'Will affect performance.')


1
EC-Earth-Consortium.50 km.EC-Earth3P-HR.r1i1p2f1.gr.hist-1950_highres-future_1950-2022


/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/smm.py:130: UserWarning: Input array is not C_CONTIGUOUS. Will affect performance.
  warnings.warn('Input array is not C_CONTIGUOUS. ' 'Will affect performance.')


2
CNRM-CERFACS.250 km.CNRM-CM6-1.r2i1p1f2.gr.highresSST-present_highresSST-future_1950-2022


...

1
ECMWF.25 km.ERA5.1950-2022


/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/smm.py:130: UserWarning: Input array is not C_CONTIGUOUS. Will affect performance.
  warnings.warn('Input array is not C_CONTIGUOUS. ' 'Will affect performance.')


2
JRA.25 km.JRA55_6hr.1958-2022


/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/smm.py:130: UserWarning: Input array is not C_CONTIGUOUS. Will affect performance.
  warnings.warn('Input array is not C_CONTIGUOUS. ' 'Will affect performance.')


3
ECA.25 km.eobs.1950-2022


In [10]:
percs_models = percs_models.sel(year=slice(startyear,endyear))
percs_obs = percs_obs.sel(year=slice(startyear,endyear))


### Load model/obs trends of yearly percentiles

In [9]:
# Regrid and concat model and obs percentile trends

path = f'/data0/samuelb/percs/tx/{trendcovariate}trends/{trendtype}/'
# filenames_models_and_obs = [i for i in os.listdir(path) if i[-3:] == '.nc']  # ALL MODELS AND ALL OBS
filenames_models_and_obs = [i for i in os.listdir(path) if i[-12:] == f'{startyear}-{endyear}.nc']  # ALL MODELS AND ALL OBS
# filenames_models_and_obs = [i for i in os.listdir(path) if i[-12:-7] == f'{startyear}-']  # ALL MODELS AND ALL OBS, WITH VARYING END YEARS
filenames_obs = [i for i in filenames_models_and_obs if i.split('.')[2] == 'ERA5']  # JUST ERA5
# filenames_obs = [i for i in filenames_models_and_obs if i.split('.')[2] in ['ERA5','JRA55_3hr','JRA55_6hr','nclimgrid','eobs','MERRA2']]  # ALL OBS
filenames_obs.extend(['JRA.25 km.JRA55_6hr.1958-2022.nc','ECA.25 km.eobs.1958-2022.nc'])#,'NCEI.25 km.nclimgrid.1958-2022.nc','NASA.25 km.MERRA2.1980-2022.nc'])
filenames_models = [i for i in filenames_models_and_obs if i.split('.')[2] not in ['ERA5','JRA55_3hr','JRA55_6hr','nclimgrid','eobs','MERRA2']]  # EXCLUDE ALL OBS
filenames_models = [filename for filename in filenames_models if ('CESM2-CAM6' not in filename) and ('ECHAM5' not in filename)]  # EXCLUDE LEs
filenames_les = [filename for filename in [i for i in os.listdir(path) if i[-3:] == '.nc'] if (('CESM2-CAM6' in filename) and ('1958-2021' in filename)) or (('ECHAM5' in filename) and ('1958-2020' in filename))]
# filenames_models.extend(filenames_les) # INCLUDE LEs IN MODELS?
print(filenames_obs); print('\n'.join(['.'.join(i.split('.')[:]) for i in filenames_models])); print(len(filenames_models))
trends_models = regrid_and_concat(path,filenames_models,'polyfit_coefficients',res); trends_models = trends_models.assign_coords(longitude = (trends_models.coords['longitude'] + 180) % 360 - 180).sortby('longitude')
trends_obs = regrid_and_concat(path,filenames_obs,'polyfit_coefficients',res); trends_obs = trends_obs.where(trends_obs!=0).assign_coords(longitude = (trends_obs.coords['longitude'] + 180) % 360 - 180).sortby('longitude')

# regrid and concat obs trend spread

path = f'/data0/samuelb/percs/tx/{trendcovariate}trends/{trendtype}/trendspreads/'
filenames = [i for i in os.listdir(path) if i[-12:] == f'{startyear}-{endyear}.nc']
print(filenames)
trendspreads_obs = regrid_and_concat(path,filenames,'polyfit_coefficients',res); trendspreads_obs = trendspreads_obs.where(trendspreads_obs!=0).assign_coords(longitude = (trendspreads_obs.coords['longitude'] + 180) % 360 - 180).sortby('longitude')

if singleptile:
    trends_models = trends_models.sel(quantile=singleptilenum/100).squeeze()
    trends_obs = trends_obs.sel(quantile=singleptilenum/100).squeeze()
    trendspreads_obs = trendspreads_obs.sel(quantiles=singleptilenum/100).squeeze()


['ECMWF.25 km.ERA5.1958-2022.nc', 'JRA.25 km.JRA55_6hr.1958-2022.nc', 'ECA.25 km.eobs.1958-2022.nc']
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r9i1p1f2.gr.highresSST-present_highresSST-future_1958-2022.nc
MPI-M.100 km.MPI-ESM1-2-HR.r1i1p1f1.gn.highresSST-present_highresSST-future_1958-2022.nc
EC-Earth-Consortium.100 km.EC-Earth3P.r1i1p1f1.gr.highresSST-present_highresSST-future_1958-2022.nc
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r8i1p1f2.gr.highresSST-present_highresSST-future_1958-2022.nc
MPI-M.50 km.MPI-ESM1-2-XR.r1i1p1f1.gn.hist-1950_highres-future_1958-2022.nc
NOAA-GFDL.100 km.GFDL-CM4C192.r1i1p1f1.gr3.highresSST-present_highresSST-future_1958-2022.nc
CNRM-CERFACS.250 km.CNRM-CM6-1.r3i1p1f2.gr.hist-1950_highres-future_1958-2022.nc
CAS.100 km.FGOALS-f3-L.r1i1p1f1.gr.highresSST-present_highresSST-future_1958-2022.nc
MOHC.100 km.HadGEM3-GC31-MM.r1i1p1f1.gn.hist-1950_highres-future_1958-2022.nc
MIROC.50 km.NICAM16-8S.r1i1p1f1.gr.highresSST-present_highresSST-future_1958-2022.nc
MOHC.50 km.HadGEM3-GC3

/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/backend.py:56: UserWarning: Latitude is outside of [-90, 90]
  warnings.warn('Latitude is outside of [-90, 90]')


9
MOHC.100 km.HadGEM3-GC31-MM.r1i1p1f1.gn.hist-1950_highres-future_1958-2022
10
MIROC.50 km.NICAM16-8S.r1i1p1f1.gr.highresSST-present_highresSST-future_1958-2022
11
MOHC.50 km.HadGEM3-GC31-HM.r1i1p1f1.gn.highresSST-present_highresSST-future_1958-2022
12
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r10i1p1f2.gr.highresSST-present_highresSST-future_1958-2022
13
CNRM-CERFACS.250 km.CNRM-CM6-1.r9i1p1f2.gr.highresSST-present_highresSST-future_1958-2022
14
CNRM-CERFACS.250 km.CNRM-CM6-1.r8i1p1f2.gr.highresSST-present_highresSST-future_1958-2022
15
MOHC.250 km.HadGEM3-GC31-LM.r1i1p1f1.gn.highresSST-present_highresSST-future_1958-2022
16
MPI-M.100 km.MPI-ESM1-2-HR.r1i1p1f1.gn.hist-1950_highres-future_1958-2022
17
MOHC.250 km.HadGEM3-GC31-LL.r1i1p1f1.gn.hist-1950_highres-future_1958-2022
18
EC-Earth-Consortium.50 km.EC-Earth3P-HR.r3i1p2f1.gr.hist-1950_highres-future_1958-2022
19
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r3i1p1f2.gr.hist-1950_highres-future_1958-2022
20
MRI.25 km.MRI-AGCM3-2-S.r1i1p1f1.gn.highresSST

/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/backend.py:56: UserWarning: Latitude is outside of [-90, 90]
  warnings.warn('Latitude is outside of [-90, 90]')


29
MOHC.100 km.HadGEM3-GC31-MM.r1i2p1f1.gn.hist-1950_highres-future_1958-2022
30
MOHC.250 km.HadGEM3-GC31-LL.r1i3p1f1.gn.hist-1950_highres-future_1958-2022
31
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r5i1p1f2.gr.highresSST-present_highresSST-future_1958-2022
32
CNRM-CERFACS.250 km.CNRM-CM6-1.r2i1p1f2.gr.highresSST-present_highresSST-future_1958-2022
33
EC-Earth-Consortium.100 km.EC-Earth3P.r1i1p2f1.gr.hist-1950_highres-future_1958-2022
34
CNRM-CERFACS.250 km.CNRM-CM6-1.r3i1p1f2.gr.highresSST-present_highresSST-future_1958-2022
35
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r4i1p1f2.gr.highresSST-present_highresSST-future_1958-2022
36
EC-Earth-Consortium.50 km.EC-Earth3P-HR.r1i1p1f1.gr.highresSST-present_highresSST-future_1958-2022
37
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r2i1p1f2.gr.hist-1950_highres-future_1958-2022
38
MOHC.250 km.HadGEM3-GC31-LL.r1i2p1f1.gn.hist-1950_highres-future_1958-2022
39
CNRM-CERFACS.250 km.CNRM-CM6-1.r6i1p1f2.gr.highresSST-present_highresSST-future_1958-2022


...

40
MOHC.100 km.HadGEM3-GC31-MM.r1i1p1f1.gn.highresSST-present_highresSST-future_1958-2022
41
EC-Earth-Consortium.50 km.EC-Earth3P-HR.r2i1p2f1.gr.hist-1950_highres-future_1958-2022
42
EC-Earth-Consortium.100 km.EC-Earth3P.r2i1p2f1.gr.hist-1950_highres-future_1958-2022
43
CNRM-CERFACS.250 km.CNRM-CM6-1.r5i1p1f2.gr.highresSST-present_highresSST-future_1958-2022
44
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r2i1p1f2.gr.highresSST-present_highresSST-future_1958-2022
45
AS-RCEC.50 km.HiRAM-SIT-LR.r1i1p1f1.gn.highresSST-present_highresSST-future_1958-2022
46
MRI.25 km.MRI-AGCM3-2-H.r1i1p1f1.gn.highresSST-present_highresSST-future_1958-2022
47
MIROC.100 km.NICAM16-7S.r1i1p1f1.gr.highresSST-present_highresSST-future_1958-2022
48
CNRM-CERFACS.50 km.CNRM-CM6-1-HR.r3i1p1f2.gr.highresSST-present_highresSST-future_1958-2022
49
CNRM-CERFACS.250 km.CNRM-CM6-1.r4i1p1f2.gr.highresSST-present_highresSST-future_1958-2022


/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/backend.py:56: UserWarning: Latitude is outside of [-90, 90]
  warnings.warn('Latitude is outside of [-90, 90]')
/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/smm.py:130: UserWarning: Input array is not C_CONTIGUOUS. Will affect performance.
  warnings.warn('Input array is not C_CONTIGUOUS. ' 'Will affect performance.')


1
ECMWF.25 km.ERA5.1958-2022
2
JRA.25 km.JRA55_6hr.1958-2022
3
ECA.25 km.eobs.1958-2022
['ECMWF.25 km.ERA5.1958-2022.nc', 'JRA.25 km.JRA55_6hr.1958-2022.nc']


/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/backend.py:56: UserWarning: Latitude is outside of [-90, 90]
  warnings.warn('Latitude is outside of [-90, 90]')
/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/smm.py:130: UserWarning: Input array is not C_CONTIGUOUS. Will affect performance.
  warnings.warn('Input array is not C_CONTIGUOUS. ' 'Will affect performance.')


1
ECMWF.25 km.ERA5.1958-2022
2
JRA.25 km.JRA55_6hr.1958-2022


In [11]:
# Regrid era5 land-sea mask

lsm_era5 = xr.open_dataarray('/data0/samuelb/era5_lsm.nc')
lsm_era5 = lsm_era5.squeeze().assign_coords(longitude=(lsm_era5.longitude % 360)).sortby('longitude')
regridder = xe.Regridder(lsm_era5, xr.Dataset({'latitude': (['latitude'], np.arange(-90+res/2, 90, res), {'units':'degrees_north'}),'longitude': (['longitude'], np.arange(0+res/2, 360, res), {'units':'degrees_east'})}), 'conservative', weights=f'/data0/samuelb/regridders/ERA5_to_{res}deg.nc')
lsm = regridder(lsm_era5, keep_attrs=True); lsm = lsm.assign_coords(longitude = (lsm.coords['longitude'] + 180) % 360 - 180).sortby('longitude')


/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/xesmf/backend.py:56: UserWarning: Latitude is outside of [-90, 90]
  warnings.warn('Latitude is outside of [-90, 90]')


### Set regions

In [12]:
# 8 objective plus 4 cold-spot regions

regions = ['europe',
           'china',
           'argentina',
           'oman',
           'australia',
           'japan',
           'arctic',
           'nwcanada',
           'nafrica',
           'central siberia',
           'eastern siberia',
           'gris']
regtitles = ['Northwest Europe',
             'Central China',
             'Southern South America',
             'Arabian Peninsula',
             'Eastern Australia',
             'Japan/Korea',
             'Arctic Canada/Greenland',
             'Northwest Canada',
             'North Africa',
             'Central Siberia',
             'Eastern Siberia',
             'Greenland Ice Sheet']
reglats = [[45,58],
           [27,37],
           [-53,-35],
           [15,25],
           [-40,-30],
           [30,39],
           [78,85],
           [62,72],
           [20,35],
           [55,70],
           [65,75],
           [64,75]]
reglons = [[-5,12],
           [95,110],
           [-77,-66],
           [45,60],
           [135,150],
           [125,142],
           [-95,-10],
           [-135,-115],
           [10,35],
           [75,100],
           [120,140],
           [-50,-40]]


In [56]:
# 8 objective plus 2 cold-spot regions

regions = ['europe',
           'china',
           'argentina',
           'oman',
           'australia',
           'japan',
           'arctic',
           'nwcanada',
           'nafrica',
           'siberia']
regtitles = ['Northwest Europe',
             'Central China',
             'Southern S. America',
             'Arabian Peninsula',
             'Eastern Australia',
             'Japan/Korea',
             'High Arctic',
             'Northwest Canada',
             'North Africa',
             'Siberia']
reglats = [[45,58],
           [27,37],
           [-53,-35],
           [15,25],
           [-40,-30],
           [30,39],
           [78,85],
           [62,72],
           [20,35],
           [55,75]]
reglons = [[-5,12],
           [95,110],
           [-77,-66],
           [45,60],
           [135,150],
           [125,142],
           [-95,-10],
           [-135,-115],
           [10,35],
           [75,140]]


In [57]:
# Just 2 cold-spot regions

badregions = ['nafrica',
              'siberia']
badregtitles = ['North Africa',
                'Siberia']
badreglats = [[20,35],
              [55,75]]
badreglons = [[10,35],
              [75,140]]


In [58]:
regranges = [(slice(reglat[0],reglat[1]),slice(reglon[0],reglon[1])) for reglat,reglon in zip(reglats,reglons)]


In [14]:
landthresh = 0.25
summertrendthresh = (percs_obs.sel(key=f'ECMWF.25 km.ERA5.1950-2022').sel(quantile=.875).sel().polyfit(trendcovariate,1).sel(degree=1).polyfit_coefficients>0).squeeze().compute()


In [15]:
summertrendthresh_mod = (percs_models.sel(quantile=.875).polyfit(trendcovariate,1).sel(degree=1).polyfit_coefficients>0).squeeze().compute()


# Boxplots

In [42]:
# Bootstrapping for CIs

iterations = 10000

if singleptile:
    globalpercs = percs_obs.sel(quantile=singleptilenum/100).where((lsm>landthresh) & summertrendthresh)
else:
    globalpercs = percs_obs.sel(quantile=[lowerptilenum/100,upperptilenum/100]).diff('quantile').squeeze().where((lsm>landthresh) & summertrendthresh)

trendspreads_obs_regional_list = []
for regrange,region in zip(regranges,regions):
    regseries = globalpercs.sel(latitude=regrange[0],longitude=regrange[1]).weighted(weights).mean(('latitude','longitude'))
    x,y = regseries[trendcovariate],regseries
    idxs = np.random.default_rng().choice(x.values,(iterations,len(x)))
    trends = xr.concat([y.sel({trendcovariate:idxs[n]}).polyfit(trendcovariate,1).sel(degree=1).polyfit_coefficients for n in range(iterations)],'iterations')
    trends = trends.assign_coords(iterations=trends.iterations)
    trendspreads_obs_regional_list.append(trends.quantile([.025,.05,.95,.975],'iterations'))
    print(region+'     done')
trendspreads_obs_regional = dict(zip(regions,trendspreads_obs_regional_list))


europe     done


/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/numpy/lib/nanfunctions.py:1577: RuntimeWarning: All-NaN slice encountered
  result = np.apply_along_axis(_nanquantile_1d, axis, a, q,


china     done


/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/numpy/lib/nanfunctions.py:1577: RuntimeWarning: All-NaN slice encountered
  result = np.apply_along_axis(_nanquantile_1d, axis, a, q,


argentina     done


...

/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/numpy/lib/nanfunctions.py:1577: RuntimeWarning: All-NaN slice encountered
  result = np.apply_along_axis(_nanquantile_1d, axis, a, q,


nwcanada     done


/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/numpy/lib/nanfunctions.py:1577: RuntimeWarning: All-NaN slice encountered
  result = np.apply_along_axis(_nanquantile_1d, axis, a, q,


nafrica     done
siberia     done


/home/samuelb/.conda/envs/cmip6/lib/python3.10/site-packages/numpy/lib/nanfunctions.py:1577: RuntimeWarning: All-NaN slice encountered
  result = np.apply_along_axis(_nanquantile_1d, axis, a, q,


In [43]:
obscolor = {'ECMWF.25 km.ERA5.1950-2022':'tab:red',
            'ECMWF.25 km.ERA5.1958-2022':'tab:red',
            'ECMWF.25 km.ERA5.1958-2020':'tab:red',
            'JRA.25 km.JRA55_6hr.1958-2022':'tab:orange',
            'JRA.25 km.JRA55_6hr.1958-2020':'tab:orange',
            'NCEI.25 km.nclimgrid.1951-2022':'tab:brown',
            'NCEI.25 km.nclimgrid.1958-2022':'tab:brown',
            'ECA.25 km.eobs.1950-2022':'xkcd:goldenrod',
            'ECA.25 km.eobs.1958-2022':'xkcd:goldenrod',
            'ECA.25 km.eobs.1958-2020':'xkcd:goldenrod',
            'NASA.25 km.MERRA2.1980-2022':'xkcd:reddish purple'}
obsls = {'ECMWF.25 km.ERA5.1950-2022':'-',
         'ECMWF.25 km.ERA5.1958-2022':'-',
         'ECMWF.25 km.ERA5.1958-2020':'-',
         'JRA.25 km.JRA55_6hr.1958-2022':'-',
         'JRA.25 km.JRA55_6hr.1958-2020':'-',
         'NCEI.25 km.nclimgrid.1951-2022':'-',
         'NCEI.25 km.nclimgrid.1958-2022':'-',
         'ECA.25 km.eobs.1950-2022':'-',
         'ECA.25 km.eobs.1958-2022':'-',
         'ECA.25 km.eobs.1958-2020':'-',
         'NASA.25 km.MERRA2.1980-2022':'--'}
obsexcluded = ['NCEI.25 km.nclimgrid.1951-2022','NCEI.25 km.nclimgrid.1958-2022','NASA.25 km.MERRA2.1980-2022','ECMWF.25 km.ERA5.1958-2020']


In [137]:
qq_models = trends_models*trendfactor
qq_obs = trends_obs.drop_sel(key=obsexcluded,errors='ignore')*trendfactor
qq_obs_spread = dict([(key,item.drop_sel(key=obsexcluded,errors='ignore')) for (key,item) in trendspreads_obs_regional.items()])
alpha = .05
subplotheight = 3
panellabels = [letter for letter in ascii_lowercase[1:][:len(regions)]]
numrows,numcols = 2,5
sizefactor = .88 # for publication
figsize = (16.5*sizefactor,subplotheight*numrows*1.33*sizefactor)

explabel = {'highresSST-present':f'SST-forced\nmodels',
            'highresSST-present_highresSST-future_1950-2022':f'SST-forced\nmodels',
            'highresSST-present_highresSST-future_1958-2022':f'SST-forced\n',
            'highresSST-present_highresSST-future_1958-2020':f'SST-forced\nmodels',
            'highresSST-present_highresSST-future_ersstv5_1950-2021':f'SST-forced\nLE\n(CAM6/\nERSSTv5)',
            'highresSST-present_highresSST-future_ersstv5_1950-2020':f'SST-forced\nLE\n(ECHAM5/\nERSSTv5)',
            'highresSST-present_highresSST-future_hurrell_1950-2020':f'SST-forced\nLE\n(ECHAM5/\nHurrell)',
            'highresSST-present_highresSST-future_ersstv5_1958-2021':f'SST-forced\nLE\n(CAM6/\nERSSTv5)',
            'highresSST-present_highresSST-future_ersstv5_1958-2020':f'SST-forced\nLE\n(ECHAM5/\nERSSTv5)',            
            'highresSST-present_highresSST-future_hurrell_1958-2020':f'SST-forced\nLE\n(ECHAM5/\nHurrell)',
            'CAM6':f'SST-forced\nLE\n(CAM6/\nERSSTv5)',
            'hist-1950':f'Coupled\nmodels',
            'hist-1950_highres-future_1950-2022':f'Coupled\nmodels',
            'hist-1950_highres-future_1958-2022':f'Coupled\n',
            'hist-1950_highres-future_1958-2020':f'Coupled\nmodels',
            'hi':f'All ',
            'ERA5':'ERA5',
            'JRA55_6hr':'JRA55 (6hr)',
            'nclimgrid':'nClimGrid',
            'eobs':'E-OBS',
            'MERRA2':'MERRA2\n(1980–)'}
experiments = ['hist-1950_highres-future_1958-2022','highresSST-present_highresSST-future_1958-2022','hi']
subexperiments = ['hi','hi','hi']

fig,axs = plt.subplots(numrows,numcols,figsize=figsize,sharey=False,sharex=False,dpi=300)
plt.subplots_adjust(wspace=.25)
plt.subplots_adjust(hspace=.45)
modexps = [i for i in [qq_models.loc[[i for i in qq_models.key.values if experiment in i and subexperiment in i]] for experiment,subexperiment in zip(experiments,subexperiments)]]
for panellabel,region,regtitle,regrange,ax in zip(panellabels,regions,regtitles,regranges,axs.flat):
    ax.axvspan(.7,3.3,facecolor='.96')
    ax.grid(which='both',c='.9')
    ax.axhline(c='.8')
    
    # Plot models and empty space for obs
    modexp = [i.where((lsm>landthresh) & summertrendthresh).sel(latitude=regrange[0],longitude=regrange[1]).weighted(weights).mean(('latitude','longitude')) for i in modexps]
    ax.boxplot(modexp+[np.nan],widths=.4,capwidths=.3,showmeans=False,medianprops={'color':'0','zorder':2},whis=(5,95),showfliers=False,positions=[1,1.9,2.8,3.7])
    for i,modexpvals in zip([0,.9,1.8],modexp):#enumerate(modexp):#zip([-.1,.8,1.7],modexp):    
        # Plot x's:
        ax.scatter([i+1]*len(modexpvals),modexpvals,facecolors='0',marker='x',linewidth=.5,zorder=2)
    # Plot obs
    obs = qq_obs.where((lsm>landthresh) & summertrendthresh).sel(latitude=regrange[0],longitude=regrange[1]).weighted(weights).mean(('latitude','longitude')).dropna('key')
    obsx = np.linspace(len(modexp)+.6,len(modexp)+.6+len(obs)*.2,len(obs))    #.8
    color = [obscolor[val] for val in obs.key.values]; ls = [obsls[val] for val in obs.key.values]
    # ax.plot(obsx,obs,'x',c='tab:red',markersize=10)
    ax.scatter(obsx,obs,100,color,marker='x',ls=ls,lw=1,zorder=2)
    obs_low = qq_obs_spread[region].sel(quantile=alpha/2).dropna('key')*trendfactor
    obs_high = qq_obs_spread[region].sel(quantile=1-alpha/2).dropna('key')*trendfactor
    ax.vlines(obsx,obs_low,obs_high,color=color,ls=ls,lw=1)
    
    ax.set_ylabel('')
    ax.set_xticks(np.concatenate(([1,1.9,2.8],obsx)))
    ax.set_xticklabels([f'{explabel[experiment]}($n$={len(modexpvals)})' for experiment,modexpvals in zip(experiments,modexp)] + [explabel[val] for val in [val.split('.')[2] for val in obs.key.values]])#,fontsize=8.1)
    [label.set_rotation(45) for label in ax.get_xticklabels()]#[-len(obs.key):]]
    [label.set_ha('right') for label in ax.get_xticklabels()]#[-len(obs.key):]]
    [label.set_rotation_mode('anchor') for label in ax.get_xticklabels()]#[-len(obs.key):]]
    ax.set_title(panellabel,weight='bold',loc='left')
    ax.set_title(regtitle,style='italic',loc='right')
    ax.yaxis.set_major_locator(ticker.MultipleLocator(1/trendfactor))
    ax.yaxis.set_minor_locator(ticker.MultipleLocator(.5/trendfactor))
    ax.set_xlim(.7,max(obsx)+.2)
    
    if region in badregions: 
        [spine.set_color('xkcd:bright blue') for spine in list(ax.spines.values())]
        [spine.set_linewidth(1) for spine in list(ax.spines.values())]
        
axs.flat[0].annotate('Models',(.36,.93),xycoords='axes fraction',ha='center',va='center',color='.5')

if singleptile:
    axs.flat[0].set_ylabel(f'Quantile trend [°C/decade]')
    plt.suptitle(f'Yearly {singleptilenum}%ile of daily-max temperature',horizontalalignment='left',weight='bold',x=.122,y=1.05)
else:
    axs.flat[0].set_ylabel(f'Trend in yearly {upperptilenum}%ile minus\nyearly {lowerptilenum}%ile of Tx [°C/{"decade" if trendcovariate == "year" else "°C GMST"}]')    
    if numrows>1:
        axs.flat[int(len(regions)/2)].set_ylabel(f'Trend in yearly {upperptilenum}%ile minus\nyearly {lowerptilenum}%ile of Tx [°C/{"decade" if trendcovariate == "year" else "°C GMST"}]')
    plt.suptitle(f'Regional averages of trend in temperature upper tail width',horizontalalignment='left',x=.1245,y=.94) #1  #.98
    

<Figure size 4356x2106.72 with 10 Axes>

# Time series

In [139]:
modarray = percs_models.sel(quantile=[lowerptilenum/100,upperptilenum/100]).diff('quantile').squeeze().where((lsm>landthresh) & summertrendthresh)
obsarray = percs_obs.drop_sel(key=obsexcluded,errors='ignore').sel(quantile=[lowerptilenum/100,upperptilenum/100]).diff('quantile').squeeze().where((lsm>landthresh) & summertrendthresh)
    

In [144]:
subplotwidth = 4*1.25
subplotheight = 3
panellabels = [letter for letter in ascii_lowercase[1:][:len(regions)]]
numrows,numcols = 2,5
alpha = .05
relativeyear = 1958
sizefactor = .88 # for publication
figsize = (16.5*sizefactor,subplotheight*numrows*1.25*sizefactor)

fig,axs = plt.subplots(numrows,numcols,figsize=figsize,sharey=False,sharex=True,dpi=300)#subplotwidth*ncols
plt.subplots_adjust(wspace=.25)
plt.subplots_adjust(hspace=.15)

for panellabel,region,regtitle,regrange,ax in zip(panellabels,regions,regtitles,regranges,axs.flat):
    ax.grid(which='both',c='.9')
    modseries = modarray.sel(latitude=regrange[0],longitude=regrange[1]).weighted(weights).mean(('latitude','longitude'))
    obsseries = obsarray.sel(latitude=regrange[0],longitude=regrange[1]).weighted(weights).mean(('latitude','longitude'))
    
    obsseries_anom = obsseries - obsseries.mean(trendcovariate)
    obsseries_anom = obsseries_anom - xr.polyval(obsseries_anom[trendcovariate],obsseries_anom.polyfit(trendcovariate,1)).polyfit_coefficients.sel(year=relativeyear)#.values
    for k in percs_models.key:#[:2]:
        modseries_anom = modseries.sel(key=k).swap_dims({'year':trendcovariate}) - modseries.sel(key=k).swap_dims({'year':trendcovariate}).mean(trendcovariate)
        modseries_anom = modseries_anom - xr.polyval(modseries_anom[trendcovariate],modseries_anom.polyfit(trendcovariate,1)).polyfit_coefficients.sel(year=relativeyear).values
        sns.regplot(ax=ax,x=modseries_anom[trendcovariate],y=modseries_anom,scatter=False,ci=None,line_kws={'color':'0.7','lw':.5})
    hue_regplot(obsseries_anom.to_dataframe(name='tasmax').reset_index(['year','key']),x=obsseries_anom[trendcovariate] - obsseries_anom[trendcovariate].mean()*(trendcovariate=='gmst'),y='tasmax',hue='key',palette=obscolor,ci=100-alpha*100,scatter=False,ax=ax)#,scatter_kws={'color':'tab:red','s':4,'zorder':502})
    plt.setp(ax.collections[-int((~obsseries_anom.isel(year=-1).isnull()).sum().values):], alpha=.1, zorder=500)

    ax.set_xlim(-.8,1.3)
    ax.yaxis.set_major_locator(ticker.MultipleLocator(1))
    ax.yaxis.set_minor_locator(ticker.MultipleLocator(.5))
    ax.yaxis.set_major_formatter(ticker.FormatStrFormatter('$%+.1f$'))
    ax.set_xlabel('GMST (time-mean removed) [°C]')
    if trendcovariate=='year':
        [obsseries_anom.sel(key=key).plot(ax=ax,color=obscolor[key],ls=obsls[key],lw=.75,zorder=501) for key in obsseries_anom.key.values]
        ax.set_xlim(startyear-2,endyear+2)
        ax.set_xlabel('Year')
    ax.set_ylabel('')
    ax.set_title('')
    ax.set_title(panellabel,weight='bold',loc='left')
    ax.set_title(regtitle,style='italic',loc='right')
    
    if region in badregions: 
        [spine.set_color('xkcd:bright blue') for spine in list(ax.spines.values())]
        [spine.set_linewidth(1) for spine in list(ax.spines.values())]

axs.flat[0].legend(handles=[Line2D([],[],lw=.5,label='All models',color='0.7')]+[Line2D([],[],lw=1,ls=obsls[key],label=explabel[val],color=obscolor[key]) for val,key in zip([val.split('.')[2] for val in obsseries_anom.key.values],obsseries_anom.key.values)],loc='upper left',framealpha=.5).set_zorder(505)
if singleptile:
    axs.flat[0].set_ylabel(f'Quantile temperature [°C]')
    axs.flat[0].set_title(f'Regional averages of quantile temperatures (time-mean removed)',loc='left',y=1.075)
else:
    axs.flat[0].set_ylabel(f'Yearly {upperptilenum}%ile minus yearly {lowerptilenum}%ile\nof Tx (change since {relativeyear}) [°C]')
    if numrows>1:
        axs.flat[int(len(regions)/2)].set_ylabel(f'Yearly {upperptilenum}%ile minus yearly {lowerptilenum}%ile\nof Tx (change since {relativeyear}) [°C]')
        [axs.flat[i].set_xlabel('') for i in range(numcols)]
    plt.suptitle(f'Regional average change in temperature upper tail width',horizontalalignment='left',x=.1245,y=.94)
    

<Figure size 4356x1980 with 10 Axes>

# Maps

In [151]:
qq = trends_obs.sel(key=f'ECMWF.25 km.ERA5.{startyear}-{endyear}').where((lsm>landthresh) & summertrendthresh).squeeze()*trendfactor
alpha=.05
qq_sig = cyclic_dataarray((((trendspreads_obs.sel(key=f'ECMWF.25 km.ERA5.{startyear}-{endyear}').sel(quantile=alpha/2)>0) & (qq>0)) | ((trendspreads_obs.sel(key=f'ECMWF.25 km.ERA5.{startyear}-{endyear}').sel(quantile=1-alpha/2)<0) & (qq<0))).where((lsm>landthresh) & summertrendthresh).squeeze(),'longitude')
panellabels = [letter for letter in ascii_lowercase[1:][:len(regions)]]
sizeadjust = .9 #1 #.75
figsize = (19*sizeadjust,10*sizeadjust) #FOR MAIN    18
vmax = .25

projection = ccrs.Robinson(central_longitude=10)
fig,ax = plt.subplots(1,1,subplot_kw={'projection':projection,'frameon':False},figsize=figsize,dpi=900)
pp = qq.plot.pcolormesh(ax=ax,levels=11,vmax=vmax,vmin=-vmax,cmap='coolwarm',extend='both',transform=ccrs.PlateCarree(),cbar_kwargs={'label':f'Trend in yearly {upperptilenum}%ile minus\nyearly {lowerptilenum}%ile of Tx [°C/{"decade" if trendcovariate == "year" else "°C GMST"}]','orientation':'vertical','shrink':.55,'aspect':25,'pad':.03},linewidth=0,rasterized=True); pp.set_edgecolor('face')#'orientation':'horizontal','shrink':.75,'aspect':35,'pad':0
stacked = qq_sig.stack(x=['longitude','latitude']); ax.scatter(stacked[stacked<1].longitude,stacked[stacked<1].latitude,marker='o',linewidth=.2,edgecolor='none',facecolor='1',s=3*np.cos(np.deg2rad(stacked[stacked<1].latitude)),transform=ccrs.PlateCarree()) #s=1.5*np.cos(np.deg2rad(stacked[stacked<1].latitude) or 2 or 3
for region,reglat,reglon,panellabel in zip(regions,reglats,reglons,panellabels):
    ax.plot([reglon[0],reglon[1],reglon[1],reglon[0],reglon[0]],[reglat[0],reglat[0],reglat[1],reglat[1],reglat[0]],color='1',lw=1.75,transform=ccrs.PlateCarree())
    if region not in badregions: ax.plot([reglon[0],reglon[1],reglon[1],reglon[0],reglon[0]],[reglat[0],reglat[0],reglat[1],reglat[1],reglat[0]],color='0',lw=.75,transform=ccrs.PlateCarree())
    else: ax.plot([reglon[0],reglon[1],reglon[1],reglon[0],reglon[0]],[reglat[0],reglat[0],reglat[1],reglat[1],reglat[0]],color='xkcd:bright blue',lw=.875,transform=ccrs.PlateCarree())
    ax.annotate(panellabel,(reglon[0],reglat[1]),xycoords=ccrs.PlateCarree(),ha='left',va='bottom',fontsize='medium',fontweight='bold',path_effects=[pe.withStroke(linewidth=1,foreground='1')])
ax.set_extent((-120,167,-55,90))
ax.coastlines('50m',color='0',lw=.2); ax.add_feature(cfeature.NaturalEarthFeature(category='cultural',name='admin_0_boundary_lines_land',facecolor='none',scale='50m',edgecolor='0',lw=.2)); ax.add_feature(cfeature.LAKES.with_scale('110m'),edgecolor='0',facecolor='none',lw=.2); ax.add_feature(cfeature.STATES.with_scale('110m'),edgecolor='0',facecolor='none',lw=.2); ax.add_feature(cfeature.RIVERS.with_scale('110m'),edgecolor='tab:blue',facecolor='none',lw=.4)
cmap2 = plt.colormaps.get_cmap('viridis'); cmap2.set_over('tab:gray')
pp = qq.isnull().where((qq.isnull()) & (lsm>landthresh)).plot.pcolormesh(ax=ax,levels=[0,1],cmap=cmap2,transform=ccrs.PlateCarree(),add_colorbar=False,linewidth=0,rasterized=True); pp.set_edgecolor('face')
ax.set_title(r'$\bf{a}$'+f'  Observed trend in temperature upper tail width ({startyear}–{endyear}, ERA5)')


<Figure size 15390x8100 with 2 Axes>

In [153]:
subset = trends_models
qq = (xr.concat([subset, trends_obs.sel(key=f'ECMWF.25 km.ERA5.{startyear}-{endyear}').squeeze()],'key').rank('key',pct=True).sel(key=f'ECMWF.25 km.ERA5.{startyear}-{endyear}')*100).where((lsm>landthresh) & summertrendthresh)
qq = (qq - qq.min()) / (qq.max() - qq.min())*100
panellabels = [letter for letter in ascii_lowercase[1:][:len(regions)]]
sizeadjust = .9 
figsize = (19*sizeadjust,10*sizeadjust) #FOR MAIN    #18
levels = [0.0001,5,25,75,95,100]

projection = ccrs.Robinson(central_longitude=10)
fig,ax = plt.subplots(1,1,subplot_kw={'projection':projection,'frameon':False},figsize=figsize,dpi=900)
cmap1 = plt.colormaps.get_cmap('Spectral_r')
pp = qq.plot.pcolormesh(ax=ax,levels=levels,cmap=cmap1,extend='both',transform=ccrs.PlateCarree(),add_colorbar=False,linewidth=0,rasterized=True); pp.set_edgecolor('face')#,cbar_kwargs={'label':'Percentile','orientation':'horizontal','shrink':.75,'aspect':35,'pad':0})
cb = plt.colorbar(pp,label='Percent of model trends less than observed trend [%]',orientation='vertical',shrink=.55,aspect=25,pad=.03) #,orientation='horizontal',shrink=.75,aspect=35,pad=0    #'horizontal' FOR SI #'vertical' FOR MAIN
cb.set_ticklabels(['0','5','25','75','95','100'])
for region,reglat,reglon,panellabel in zip(regions,reglats,reglons,panellabels):
    ax.plot([reglon[0],reglon[1],reglon[1],reglon[0],reglon[0]],[reglat[0],reglat[0],reglat[1],reglat[1],reglat[0]],color='1',lw=1.75,transform=ccrs.PlateCarree())
    if region not in badregions: ax.plot([reglon[0],reglon[1],reglon[1],reglon[0],reglon[0]],[reglat[0],reglat[0],reglat[1],reglat[1],reglat[0]],color='0',lw=.75,transform=ccrs.PlateCarree())
    else: ax.plot([reglon[0],reglon[1],reglon[1],reglon[0],reglon[0]],[reglat[0],reglat[0],reglat[1],reglat[1],reglat[0]],color='xkcd:bright blue',lw=.875,transform=ccrs.PlateCarree())
    ax.annotate(panellabel,(reglon[0],reglat[1]),xycoords=ccrs.PlateCarree(),ha='left',va='bottom',fontsize='medium',fontweight='bold',path_effects=[pe.withStroke(linewidth=1,foreground='1')])    
ax.set_extent((-120,167,-55,90)) # ax.set_extent((-179.9,179.9,-60,90))
ax.coastlines('50m',color='0',lw=.2); ax.add_feature(cfeature.NaturalEarthFeature(category='cultural',name='admin_0_boundary_lines_land',facecolor='none',scale='50m',edgecolor='0',lw=.2)); ax.add_feature(cfeature.LAKES.with_scale('110m'),edgecolor='0',facecolor='none',lw=.2); ax.add_feature(cfeature.STATES.with_scale('110m'),edgecolor='0',facecolor='none',lw=.2); ax.add_feature(cfeature.RIVERS.with_scale('110m'),edgecolor='tab:blue',facecolor='none',lw=.4)

cmap2 = plt.colormaps.get_cmap('viridis'); cmap2.set_over('tab:gray')
pp = qq.isnull().where((qq.isnull()) & (lsm>landthresh)).plot.pcolormesh(ax=ax,levels=[0,1],cmap=cmap2,transform=ccrs.PlateCarree(),add_colorbar=False,linewidth=0,rasterized=True); pp.set_edgecolor('face')

ax.set_title(r'$\bf{b}$  Observed trend versus model trends')


Text(0.5, 1.0, '$\\bf{b}$  Observed trend versus model trends')

<Figure size 15390x8100 with 2 Axes>

# Location-agnostic trends


In [12]:
souththresh = -60


In [17]:
histweightsmodels,histtrendsmodels = xr.broadcast(weights.sel(latitude=slice(souththresh,90)),trends_models.assign_coords({'newkey':('key',[key[:-9] for key in trends_models.key.values])}).swap_dims({'key':'newkey'}).where((lsm>landthresh) & summertrendthresh_mod.assign_coords({'newkey':('key',[key[:-9] for key in summertrendthresh_mod.key.values])}).swap_dims({'key':'newkey'})).sel(latitude=slice(souththresh,90)))
histweightsera5,histtrendsera5 = xr.broadcast(weights.sel(latitude=slice(souththresh,90)),trends_obs.sel(key='ECMWF.25 km.ERA5.1958-2022').where((lsm>landthresh) & summertrendthresh).sel(latitude=slice(souththresh,90)))


In [18]:
histweightsmodels_lowres,histtrendsmodels_lowres = xr.broadcast(weights.sel(latitude=slice(souththresh,90)),trends_models.loc[[any(res in key for res in [f'.{res} km' for res in [100,250]]) for key in trends_models.key.values]].assign_coords({'newkey':('key',[key[:-9] for key in trends_models.loc[[any(res in key for res in [f'.{res} km' for res in [100,250]]) for key in trends_models.key.values]].key.values])}).swap_dims({'key':'newkey'}).where((lsm>landthresh) & summertrendthresh_mod.assign_coords({'newkey':('key',[key[:-9] for key in summertrendthresh_mod.key.values])}).swap_dims({'key':'newkey'})).sel(latitude=slice(souththresh,90)))
histweightsmodels_hires,histtrendsmodels_hires = xr.broadcast(weights.sel(latitude=slice(souththresh,90)),trends_models.loc[[any(res in key for res in [f'.{res} km' for res in [25,50]]) for key in trends_models.key.values]].assign_coords({'newkey':('key',[key[:-9] for key in trends_models.loc[[any(res in key for res in [f'.{res} km' for res in [25,50]]) for key in trends_models.key.values]].key.values])}).swap_dims({'key':'newkey'}).where((lsm>landthresh) & summertrendthresh_mod.assign_coords({'newkey':('key',[key[:-9] for key in summertrendthresh_mod.key.values])}).swap_dims({'key':'newkey'})).sel(latitude=slice(souththresh,90)))
histweightsmodels_coupled,histtrendsmodels_coupled = xr.broadcast(weights.sel(latitude=slice(souththresh,90)),trends_models.loc[[any(exp in key for exp in ['hist-1950_highres-future_']) for key in trends_models.key.values]].assign_coords({'newkey':('key',[key[:-9] for key in trends_models.loc[[any(exp in key for exp in ['hist-1950_highres-future_']) for key in trends_models.key.values]].key.values])}).swap_dims({'key':'newkey'}).where((lsm>landthresh) & summertrendthresh_mod.assign_coords({'newkey':('key',[key[:-9] for key in summertrendthresh_mod.key.values])}).swap_dims({'key':'newkey'})).sel(latitude=slice(souththresh,90)))
histweightsmodels_sst,histtrendsmodels_sst = xr.broadcast(weights.sel(latitude=slice(souththresh,90)),trends_models.loc[[any(exp in key for exp in ['highresSST-present_highresSST-future_']) for key in trends_models.key.values]].assign_coords({'newkey':('key',[key[:-9] for key in trends_models.loc[[any(exp in key for exp in ['highresSST-present_highresSST-future_']) for key in trends_models.key.values]].key.values])}).swap_dims({'key':'newkey'}).where((lsm>landthresh) & summertrendthresh_mod.assign_coords({'newkey':('key',[key[:-9] for key in summertrendthresh_mod.key.values])}).swap_dims({'key':'newkey'})).sel(latitude=slice(souththresh,90)))


In [19]:
era5arrayunmasked = percs_obs.sel(key='ECMWF.25 km.ERA5.1950-2022').sel(year=slice(startyear,endyear)).sel(quantile=[lowerptilenum/100,upperptilenum/100]).diff('quantile').squeeze()
pvals_era5 = xr.apply_ufunc(scipylinregress_pval,era5arrayunmasked[trendcovariate],era5arrayunmasked,input_core_dims=[[trendcovariate],[trendcovariate]],vectorize=True)
histpvalsera5 = pvals_era5.where((lsm>landthresh) & summertrendthresh).sel(latitude=slice(souththresh,90))


In [21]:
modarrayunmasked = percs_models.sel(quantile=[lowerptilenum/100,upperptilenum/100]).diff('quantile').squeeze()
pvals_models = xr.apply_ufunc(scipylinregress_pval,modarrayunmasked[trendcovariate],modarrayunmasked,input_core_dims=[[trendcovariate],[trendcovariate]],vectorize=True)
histpvalsmodels = pvals_models.assign_coords({'newkey':('key',[key[:-9] for key in pvals_models.key.values])}).swap_dims({'key':'newkey'}).where((lsm>landthresh) & summertrendthresh_mod.assign_coords({'newkey':('key',[key[:-9] for key in summertrendthresh_mod.key.values])}).swap_dims({'key':'newkey'})).sel(latitude=slice(souththresh,90))


In [71]:
histtrendss = [[histtrendsmodels,histtrendsera5],
               [histtrendsmodels_lowres,histtrendsmodels_hires,histtrendsera5],
               [histtrendsmodels_coupled,histtrendsmodels_sst,histtrendsera5],
              ]
histweightss = [[histweightsmodels,histweightsera5],
                [histweightsmodels_lowres,histweightsmodels_hires,histweightsera5],
                [histweightsmodels_coupled,histweightsmodels_sst,histweightsera5],
               ]
labelss = [['All models','ERA5'],
           ['Low-res. models','Hi-res. models','ERA5'],
           ['Coupled models','SST-forced models','ERA5'],
          ]
colorss = [['0','tab:red'],
           ['0','0','tab:red'],
           ['0','0','tab:red'],
          ]
histtypess = [['step','step'],
              ['step','step','step'],
              ['step','step','step'],
             ]
linestyless = [['-','-'],
               [':','--','-'],
               [':','--','-'],
              ]
alphass = [[1,1],
           [1,1,1],
           [1,1,1],
          ]
titles = ['All models vs. ERA5',
          'Low-res. vs. Hi-res. models vs. ERA5',
          'Coupled vs. SST-forced models vs. ERA5',
         ]
step = .05
panellabels = ['a','a','a']
log = True
both = True
stat = 'density'

start = 0
howmany = 3; picker = slice(start,start+howmany)
ncols = 1
nrows = 3

fig,axs = plt.subplots(nrows,ncols,figsize=(4.45*ncols,2.83*nrows+.51),dpi=300,sharex=True,layout='constrained',squeeze=0)
for ax,histtrends,histweights,labels,colors,histtypes,linestyles,alphas,title,panellabel in zip(axs.flat,histtrendss[picker],histweightss[picker],labelss[picker],colorss[picker],histtypess[picker],linestyless[picker],alphass[picker],titles[picker],panellabels):
    ax.grid(c='.9')
    ax.axvline(0,c='.8')
    # bins = np.linspace(min([histtrend.min() for histtrend in histtrends])*1.1,max([histtrend.max() for histtrend in histtrends])*1.1,40)*10
    binsneg = np.arange(np.floor(min([histtrend.min()*10 for histtrend in histtrends])*1/step)*step-step,0,step); binspos = np.arange(0,np.ceil(max([histtrend.max()*10 for histtrend in histtrends])*1/step)*step+step,step)
    bins = np.concatenate((binsneg,binspos))
    if both == True: ax1 = ax.twinx(); ax1.tick_params(left=True,right=False,labelleft=True,labelright=False,direction='in',pad=-12,labelcolor='.7'); ax1.set_ylim((0,7)); ax1.set_yticks([1,2,3,4,5,6])
    for ii,(histtrend,histweight,label,color,histtype,linestyle,alpha) in enumerate(zip(histtrends,histweights,labels,colors,histtypes,linestyles,alphas)):
        ax.axvline(histtrend.weighted(histweight).quantile(.5)*10,color=color,lw=1,ls=linestyle)
        frame = (histtrend*10).stack({'location':('longitude','latitude')}).drop(['degree','time','latitude','longitude']).to_dataframe().join(histweight.isel(newkey=0,missing_dims='ignore').stack({'location':('longitude','latitude')}).drop_vars(['newkey','latitude','longitude'],errors='ignore').to_dataframe())
        ax.hist((histtrend*10).values.ravel()[~np.isnan(histtrend.values.ravel())],weights=histweight.values.ravel()[~np.isnan(histtrend.values.ravel())],
                label=label+f'{f" (n={len(histtrend.newkey)})" if label!="ERA5" else ""}'+'\n'+r"$(Skewness = {})$".format(np.round(weighted_skew(histtrend.values.ravel()[~np.isnan(histtrend.values.ravel())],histweight.values.ravel()[~np.isnan(histtrend.values.ravel())]),2)),  #histtrend.stack({'location':('latitude','longitude')}).dropna('location').reduce(func=stats.skew,axis=[i for i in range(len(histtrend.stack({'location':('latitude','longitude')}).dropna('location').dims))]).values
                color=color,histtype=histtype,linestyle=linestyle,alpha=alpha,
                bins=bins,log=log,density=True,zorder=3)
        if both == True:
            ax1.hist((histtrend*10).values.ravel()[~np.isnan(histtrend.values.ravel())],weights=histweight.values.ravel()[~np.isnan(histtrend.values.ravel())],
                    color=color,histtype=histtype,linestyle=linestyle,lw=.5,alpha=.5,
                    bins=bins,log=False,density=True,zorder=3)
    leg = ax.legend(loc='upper right',fontsize='small',reverse=True,markerfirst=False,framealpha=0); [t.set_ha('right') for t in leg.get_texts()]
    ax.set_title(panellabel,loc='left',fontweight='bold')
    ax.set_title(title,loc='right',fontstyle='italic')
    ax.set_xlim(-.775-.025,1.425+.025)
    ax.set_xticks([-.5,0,.5,1])
    ax.set_ylabel(f'{"Probability (bin-integrated)" if stat == "probability" else "Density"}')
axs.flat[-1].set_xlabel(f'Trend in yearly hottest {"day" if upperptilenum == 100 else f"{int(int((100-upperptilenum)*2))}% of days"} minus\nhottest {int((100-lowerptilenum)*2)}% of days [°C/{"decade" if trendcovariate == "year" else "°C GMST"}]')


Text(0.5, 0, 'Trend in yearly hottest 2% of days minus\nhottest 25% of days [°C/decade]')

<Figure size 1335x2700 with 6 Axes>

In [78]:
latslice = slice(-60,90)
histtrendss = [[histtrendsmodels.sel(latitude=latslice),histtrendsera5.sel(latitude=latslice)],
               [histtrendsmodels_lowres.sel(latitude=latslice),histtrendsmodels_hires.sel(latitude=latslice),histtrendsera5.sel(latitude=latslice)],
               [histtrendsmodels_coupled.sel(latitude=latslice),histtrendsmodels_sst.sel(latitude=latslice),histtrendsera5.sel(latitude=latslice)],
              ]
histweightss = [[histweightsmodels.sel(latitude=latslice),histweightsera5.sel(latitude=latslice)],
                [histweightsmodels_lowres.sel(latitude=latslice),histweightsmodels_hires.sel(latitude=latslice),histweightsera5.sel(latitude=latslice)],
                [histweightsmodels_coupled.sel(latitude=latslice),histweightsmodels_sst.sel(latitude=latslice),histweightsera5.sel(latitude=latslice)],
               ]
colorss = [['0','tab:red'],
           ['0','0','tab:red'],
           ['0','0','tab:red'],
          ]
linestyless = [['-','-'],
               [':','--','-'],
               [':','--','-'],
              ]
titles = ['All models vs. ERA5',
          'Low-res. vs. Hi-res. models vs. ERA5',
          'Coupled vs. SST-forced models vs. ERA5',
         ]
panellabels = [letter for letter in ascii_lowercase[1::2][:len(histtrendss)]]
           
step = .01#.01
log = True
cdftype = 'split'
enhancementx = .5

fig,axs = plt.subplots(len(histtrendss),1,figsize=(5.25,3*len(histtrendss)),dpi=300,sharex=True,layout='constrained')     #5.05

for ii,(ax,histtrends,histweights,colors,linestyles,title,panellabel) in enumerate(zip(axs.flat,histtrendss,histweightss,colorss,linestyless,titles,panellabels)):
    ax.grid(c='.9')
    ax1 = ax.twinx()
    axcolor = 'xkcd:reddish purple'
    if cdftype == 'split':
        binsneg = np.arange(np.floor(min([histtrend.min()*10 for histtrend in histtrends])*1/step)*step-step,step,step); binspos = np.arange(0,np.ceil(max([histtrend.max()*10 for histtrend in histtrends])*1/step)*step+step,step)
        bins = np.concatenate((binsneg,binspos))
        binmids = np.concatenate((binsneg[:-1]+np.diff(binsneg)/2,binspos[:-1]+np.diff(binspos)/2))
        overprobera5,_,_ = ax.hist((histtrends[-1].where(histtrends[-1]>0)*10).values.ravel()[~np.isnan(histtrends[-1].where(histtrends[-1]>0).values.ravel())],weights=histweights[-1].where(histtrends[-1]>0).values.ravel()[~np.isnan(histtrends[-1].where(histtrends[-1]>0).values.ravel())],cumulative=-1,histtype='step',bins=binspos,log=log,density=True,color='tab:red',zorder=11)
        underprobera5,_,_ = ax.hist((histtrends[-1].where(histtrends[-1]<0)*10).values.ravel()[~np.isnan(histtrends[-1].where(histtrends[-1]<0).values.ravel())],weights=histweights[-1].where(histtrends[-1]<0).values.ravel()[~np.isnan(histtrends[-1].where(histtrends[-1]<0).values.ravel())],cumulative=1,histtype='step',bins=binsneg,log=log,density=True,color='tab:red',zorder=11)           
        for histtrend,histweight,color,linestyle in zip(histtrends[:-1],histweights[:-1],colors[:-1],linestyles[:-1]):
            overprobmodels,_,_ = ax.hist((histtrend.where(histtrend>0)*10).values.ravel()[~np.isnan(histtrend.where(histtrend>0).values.ravel())],weights=histweight.where(histtrend>0).values.ravel()[~np.isnan(histtrend.where(histtrend>0).values.ravel())],cumulative=-1,histtype='step',ls=linestyle,bins=binspos,log=log,density=True,color=color,zorder=10)
            underprobmodels,_,_ = ax.hist((histtrend.where(histtrend<0)*10).values.ravel()[~np.isnan(histtrend.where(histtrend<0).values.ravel())],weights=histweight.where(histtrend<0).values.ravel()[~np.isnan(histtrend.where(histtrend<0).values.ravel())],cumulative=1,histtype='step',ls=linestyle,bins=binsneg,log=log,density=True,color=color,zorder=10)
            probratio = np.concatenate((underprobera5/underprobmodels,overprobera5/overprobmodels))
            ax1.plot(binmids,probratio,zorder=12,color=axcolor,ls=linestyle,label=r'$\frac{P(\mathrm{ERA5\ trends}<x\mathrm{, }>x)}{P(\mathrm{Model\ trends}<x\mathrm{, }>x)}$')
            if ii==0:
                enhancement = probratio[(binmids<enhancementx+step) & (binmids>enhancementx-step)].mean()
                ax1.plot(enhancementx,enhancement,'o',markersize=5,color=axcolor,markeredgecolor='0',zorder=20); ax1.annotate(f'Positive trends >{enhancementx}\n{np.round(enhancement,1)}-fold less likely\nin models',(enhancementx,enhancement),xytext=(15,-20),textcoords='offset points',arrowprops=dict(arrowstyle='->',connectionstyle='arc3,rad=-0.3',shrinkB=5),va='top',fontsize='small',path_effects=[pe.withStroke(linewidth=2,foreground='1')],zorder=13) #~{int(10**np.log10([1,2,3,4,5])[np.abs(np.log10([1,2,3,4,5])-np.log10(probratio[binmids==.5+step/2][0])).argmin()])}
        ax.set_ylabel(r'P(trends$>x$) (for positive $x$) or'+'\n'+'P(trends$<x$) (for negative $x$)')   
    elif cdftype == 'wholerange':
        binsneg = np.arange(np.floor(min([histtrend.min()*10 for histtrend in histtrends])*1/step)*step-step,-0.00001,step); binspos = np.arange(0,np.ceil(max([histtrend.max()*10 for histtrend in histtrends])*1/step)*step+step,step)
        bins = np.concatenate((binsneg,binspos))
        binmids = bins[:-1]+np.diff(bins)/2
        overproballera5,_,_ = ax.hist((histtrends[-1]*10).values.ravel()[~np.isnan(histtrends[-1].values.ravel())],weights=histweights[-1].values.ravel()[~np.isnan(histtrends[-1].values.ravel())],cumulative=-1,histtype='step',bins=bins,log=log,density=True,color='tab:red',zorder=11)   
        for histtrend,histweight,color,linestyle in zip(histtrends[:-1],histweights[:-1],colors[:-1],linestyles[:-1]):
            overproballmodels,_,_ = ax.hist((histtrend*10).values.ravel()[~np.isnan(histtrend.values.ravel())],weights=histweight.values.ravel()[~np.isnan(histtrend.values.ravel())],cumulative=-1,histtype='step',ls=linestyle,bins=bins,log=log,density=True,color=color,zorder=10)
            overprobratio = overproballera5/overproballmodels
            ax1.plot(binmids,overprobratio,zorder=12,color=axcolor,ls=linestyle,label=r'$\frac{P(\mathrm{ERA5\ trends}>x)}{P(\mathrm{Model\ trends}>x)}$')
            if ii==0:
                enhancement = overprobratio[(binmids<enhancementx+step) & (binmids>enhancementx-step)].mean()
                ax1.plot(enhancementx,enhancement,'o',markersize=5,color=axcolor,markeredgecolor='0',zorder=20); ax1.annotate(f'Trends >{enhancementx}\n{np.round(enhancement,1)}-fold less likely\nin models',(enhancementx,enhancement),xytext=(15,-20),textcoords='offset points',arrowprops=dict(arrowstyle='->',connectionstyle='arc3,rad=-0.3',shrinkB=5),va='top',fontsize='small',path_effects=[pe.withStroke(linewidth=2,foreground='1')],zorder=13) #~{int(10**np.log10([1,2,3,4,5])[np.abs(np.log10([1,2,3,4,5])-np.log10(overprobratio[binmids==.5+step/2][0])).argmin()])}
        [ax.axvline((histtrends[-1]*10).weighted(histweights[-1]).quantile(quant).values,c='.4',ls=':',lw=.75) for quant in [.99,.999,.9999]]
        ax.set_ylabel(r'P(trends$>x$)')
        if bothsign:
            underproballera5,_,_ = ax.hist((histtrends[-1]*10).values.ravel()[~np.isnan(histtrends[-1].values.ravel())],weights=histweights[-1].values.ravel()[~np.isnan(histtrends[-1].values.ravel())],cumulative=1,histtype='step',alpha=.5,lw=.5,bins=bins,log=log,density=True,color='tab:red',zorder=11)
            for histtrend,histweight,color,linestyle in zip(histtrends[:-1],histweights[:-1],colors[:-1],linestyles[:-1]):
                underproballmodels,_,_ = ax.hist((histtrend*10).values.ravel()[~np.isnan(histtrend.values.ravel())],weights=histweight.values.ravel()[~np.isnan(histtrend.values.ravel())],cumulative=1,histtype='step',ls=linestyle,alpha=.5,lw=.5,bins=bins,log=log,density=True,color=color,zorder=10)
                underprobratio = underproballera5/underproballmodels 
                ax1.plot(binmids,underprobratio,alpha=.5,lw=1,zorder=12,color=axcolor,ls=linestyle,label=r'$\frac{P(\mathrm{ERA5\ trends}<x)}{P(\mathrm{Model\ trends}<x)}$')
            [ax.axvline((histtrends[-1]*10).weighted(histweights[-1]).quantile(quant).values,c='.4',ls=':',lw=.75) for quant in [.01,.001,.0001]]
            ax.set_ylabel(r'P(trends$>x$) or P(trends$<x$)')

    ax.axvline(0,c='.8')
    ax.set_ylim((None,1))
    ax.set_xlim(-.775-.025,1.425+.025)#ax.set_xlim(-.775-.025,1.425+.025)#ax.set_xlim(-.775,1.425)#ax.set_xlim(min(bins),max(bins))
    ax.set_xticks([-.5,0,.5,1])
    ax.set_title(panellabel,loc='left',fontweight='bold')
    ax.set_title(title,loc='right',fontstyle='italic')

    ax1.axhline(1,c='.8')
    if ii==0: 
        ax1.legend(loc='lower right',fontsize='medium',edgecolor='none').set_zorder(20)
    ax1.set_yscale('log')
    ax1.set_ylim(.6,None)
    ax1.set_yticks([tick for tick in [.6,1,3,10,30,100] if tick<ax1.get_ylim()[1]])
    ax1.yaxis.set_major_formatter(ticker.FuncFormatter(lambda y, _: r'{:,.16g}$\times$'.format(y).lstrip('0')))
    ax1.yaxis.set_minor_formatter('')
    ax1.tick_params(axis='y',which='both',labelcolor=axcolor)
    ax1.set_ylabel(r'Probability ratio',color=axcolor)

axs.flat[-1].set_xlabel(f'Trend in yearly hottest {"day" if upperptilenum == 100 else f"{int(int((100-upperptilenum)*2))}% of days"} minus\nhottest {int((100-lowerptilenum)*2)}% of days [°C/{"decade" if trendcovariate == "year" else "°C GMST"}]')


/tmp/ipykernel_1044342/3111226713.py:47: RuntimeWarning: invalid value encountered in divide
  probratio = np.concatenate((underprobera5/underprobmodels,overprobera5/overprobmodels))
/tmp/ipykernel_1044342/3111226713.py:47: RuntimeWarning: invalid value encountered in divide
  probratio = np.concatenate((underprobera5/underprobmodels,overprobera5/overprobmodels))
/tmp/ipykernel_1044342/3111226713.py:47: RuntimeWarning: invalid value encountered in divide
  probratio = np.concatenate((underprobera5/underprobmodels,overprobera5/overprobmodels))
/tmp/ipykernel_1044342/3111226713.py:47: RuntimeWarning: invalid value encountered in divide
  probratio = np.concatenate((underprobera5/underprobmodels,overprobera5/overprobmodels))
/tmp/ipykernel_1044342/3111226713.py:47: RuntimeWarning: invalid value encountered in divide
  probratio = np.concatenate((underprobera5/underprobmodels,overprobera5/overprobmodels))


Text(0.5, 0, 'Trend in yearly hottest 2% of days minus\nhottest 25% of days [°C/decade]')

<Figure size 1575x2700 with 6 Axes>

In [157]:
qqs = [da_era5,
       da_models,
       da_era5-da_models,
       da_rat,
      ]
norms = [cm.LogNorm(.0001,1),
         cm.LogNorm(.0001,1),
         cm.Normalize(-.4,.4),
         cm.LogNorm(.1,10),
        ]
cmaps = ['inferno',
         'inferno',
         'coolwarm',
         'coolwarm',
        ]
if cdftype=='wholerange': 
    titles = [r'$P(\mathrm{ERA5\ trends}>x)$',
              r'$P(\mathrm{Model\ trends}>x)$',
              r'$P(\mathrm{ERA5\ trends}>x) - P(\mathrm{Model\ trends}>x)$',
              r'$\frac{P(\mathrm{ERA5\ trends}>x)}{P(\mathrm{Model\ trends}>x)}$',
             ]
if cdftype=='split': 
    titles = [r'$P(\mathrm{ERA5\ trends}<x\mathrm{, }>x)$',
              r'$P(\mathrm{Model\ trends}<x\mathrm{, }>x)$',
              r'$P(\mathrm{ERA5\ trends}<x\mathrm{, }>x) - P(\mathrm{Model\ trends}<x\mathrm{, }>x)$',
              r'$\frac{P(\mathrm{ERA5\ trends}<x\mathrm{, }>x)}{P(\mathrm{Model\ trends}<x\mathrm{, }>x)}$',
             ]
labels = ['Probability',
          'Probability',
          'Probability difference',
          'Probability ratio',
         ]
tickformats = [ticker.ScalarFormatter(),
               ticker.ScalarFormatter(),
               ticker.ScalarFormatter(),
               ticker.FuncFormatter(lambda y, _: r'{:,.2g}$\times$'.format(y).lstrip('0')),
              ]
panellabels = [letter for letter in ascii_lowercase[:len(qqs)]]

fig,axs = plt.subplots(2,2,figsize=(5*1.05*2,3.2*1.05*2),dpi=900,layout='constrained',sharex=True,sharey=True)
for ax,qq,norm,cmap,title,label,tickformat,panellabel in zip(axs.flat,qqs,norms,cmaps,titles,labels,tickformats,panellabels):
    pp = qq.plot.pcolormesh(ax=ax,norm=norm,cmap=cmap,cbar_kwargs={'label':label,'format':tickformat},zorder=2,linewidth=0,rasterized=True); pp.set_edgecolor('face')
    ax.grid(c='.9'); ax.axvline(0,c='.8'); ax.axhline(0,c='.8')
    ax.set_title(title,loc='right',style='italic',fontsize=10)
    ax.set_title(panellabel,loc='left',weight='bold')
    ax.set_ylabel('')
    ax.set_xlabel('')
    ax.set_xlim(-.775-.025,1.425+.025)
    ax.set_xticks([-.5,0,.5,1])
[axs.flat[ii].set_xlabel(f'Trend in yearly hottest {"day" if upperptilenum == 100 else f"{int(int((100-upperptilenum)*2))}% of days"} minus\nhottest {int((100-lowerptilenum)*2)}% of days [°C/{"decade" if trendcovariate == "year" else "°C GMST"}]') for ii in [-2,-1]]
axs.flat[0].set_ylabel('Latitude [°N]')
axs.flat[2].set_ylabel('Latitude [°N]')


Text(0, 0.5, 'Latitude [°N]')

<Figure size 9450x6048 with 8 Axes>